# The `pandas` library for data analysis

Powerful data analysis in Python is made easier by the `pandas` package.
Its fundamental data structure is a *data frame*, a table of data in which each column is labelled and may be of a different type. It also allows us to deal with missing data. 

In [ ]:
import numpy as np
import pandas as pd

In [ ]:
%matplotlib inline

We will use data on the number of students passing a certain course in UNAM (the National University of Mexico), given in an Excel spreadsheet.

In [ ]:
pd.read_excel?

In [ ]:
course_data = pd.read_excel("course_data.xls", 'Sheet1')

In [ ]:
type(course_data)

The original, raw data, on 10 years' worth of groups for a certain course, looks like the following. The grade is out of 10; NP means that the student enrolled but then did not present the course and 5 is a fail:

In [ ]:
course_data.head()

We can obtain a more easily-digestible summary with the `head()` member function:

In [ ]:
course_data.head()

----
**Exercise**: Looking at the data, what kind of manipulations suggest themselves?

----

In [ ]:
column_names = course_data.columns.values
column_names

Let's rename the columns to English and delete the "group" column, which is an internal number of no interest:

In [ ]:
column_names[0:4] = "semester group professor number".split()
column_names

In [ ]:
course_data.columns = column_names

del course_data["group"]  # delete the group column

course_data.head()

## Data cleaning

The word "Profesor" in each row is redundant, so we remove it:

In [ ]:
course_data["professor"]

In [ ]:
type(_)

In [ ]:
professors = [ int(professor.split()[1]) for professor in course_data["professor"] ]
course_data["professor"] = professors
course_data.head()

The semester was given in the original spreadsheet as a number:

In [ ]:
type(course_data["semester"][1])

Let's convert it to a string:

In [ ]:
semesters = [ str(int(semester)) for semester in course_data["semester"] ]
semesters = [ (semester[:-1] + "-" + semester[-1]) for semester in semesters ]
course_data["semester"] = semesters
course_data.head()

We can separate the year and odd or even semester (since in odd semesters the students are mainly repeaters) and simply add new columns to the data frame:

In [ ]:
parity = [semester[-1] for semester in course_data["semester"]]
year = [int(semester[:-2]) for semester in course_data["semester"]]

course_data["parity"] = parity
course_data["year"] = year

course_data.head()

In [ ]:
type(parity)

## Data analysis

We now would like to compute summary statistics, rearranging the data by field. This is achieved by `groupby`.

Total numbers of students in the course per year:

In [ ]:
course_data.groupby(["year"])

In [ ]:
totals = course_data.groupby(["year"]).sum()

In [ ]:
totals

In [ ]:
totals['number'].plot(marker="o")

We see that `pandas` provides a powerful and intuitive interface to `matplotlib` to easily explore data visually.

Total numbers of students separated by whether the semester is odd or even:

In [ ]:
course_data.head()

In [ ]:
even = course_data[course_data["parity"]=="2"].groupby("year").sum()  # these create new data frames
odd = course_data[course_data["parity"]=="1"].groupby("year").sum()

odd["number"].plot(marker='o')
even["number"].plot(marker='o')

del odd["professor"]
del even["professor"]


Here we used an indexing technique common in `numpy` for selecting subsets of elements from an array that satisfy certain conditions. E.g.

In [ ]:
import numpy as np

x = np.random.rand(100)

In [ ]:
x

In [ ]:
x > 0.5

In [ ]:
x[ x > 0.5 ]

In [ ]:
x = np.random.rand(100)
len(x [x > 0.5])  # those elements which are > 0.5

Let's find percentages of grades:

In [ ]:
percent_odd = odd.copy()
percent_even = even.copy()

grades = ["10", "09", "08", "07", "06", "05", "NP"]

for grade in grades:
    percent_odd[grade] /= odd["number"]
    percent_even[grade] /= even["number"]
    
del percent_even["number"]
del percent_odd["number"]

del even["number"]
del odd["number"]

even.plot(marker='o')
odd.plot(marker='o')

Percentages:

In [ ]:
percent_even.plot(marker='o')
percent_odd.plot(marker='o')

Removing the NPs:

In [ ]:
del percent_odd["NP"]
del percent_even["NP"]

percent_even.plot(marker='o')
percent_odd.plot(marker='o')

In [ ]:
professors = course_data.groupby("professor")

The number of times that each professor has taught the course:

In [ ]:
professors.count()["semester"]

In [ ]:
professors.count()